In [6]:
import pandas as pd
import numpy as np

#load data > NAME.xlsx
df = pd.read_excel('GraphMSOutput.xlsx','out_predicted_compositions')

#remove negative/false compositions
negative= df[ (df['HexNAc'] < 0) | (df['Fuc'] < 0) | (df['Hex'] < 0) | (df['NeuAc'] < 0)].index

df.drop(negative, axis=0, inplace=True)

#sort by RT and reset index
df = df.sort_values('rt_node', ascending=True)

df.reset_index(inplace=True, drop=True)

# assists grouping of the analytes into retention time clusters, neighboring RT cluster may be combined manually upon list generation

df['rt_node_round'] = df['rt_node'].round() 

threshold = 20

df['RTmin'] = [df.loc[(df['rt_node'] - t).abs() < threshold, 'rt_node_round'].min()
             for t in df['rt_node']]

df['RTmax'] = [df.loc[(df['rt_node'] - t).abs() < threshold, 'rt_node_round'].max()
             for t in df['rt_node']]

df['RT'] = ((df['RTmax']+df['RTmin'])/2).round()
df['RT'] = df['RT'].astype(str).replace('\.0', '', regex=True)

# mz instrument settings for charge state calculation 
df['mzlow'] = 400
df['mzhigh'] = 3500

# define LacyTools layout
df['# Peak'] = df['pep'] + '1' + df['composition'].str.replace(r'\W','')
df['# Peak'] = df['# Peak'].str.replace('Fuc', 'F', regex=False)
df['# Peak'] = df['# Peak'].str.replace('HexNAc', 'N', regex=False)
df['# Peak'] = df['# Peak'].str.replace('Hex', 'H', regex=False)
df['# Peak'] = df['# Peak'].str.replace('NeuAc', 'S', regex=False)

# empty by default, usually specified in LacyTools settings
df['Mass Window'] = ''

# calculation for RT window
df['Time Window'] = (threshold/2) + 5 
df['Time Window'] = df['Time Window'].astype(str).replace('\.0', '', regex=True)

# charge states, use calculation for m/z limits of instrument setting
df['Min Charge'] = 2
df['Max'] = 4
#df['Min Charge'] = (df['mz_node'] / df['mzhigh']).apply(np.ceil)
#df['Min Charge'] = df['Min Charge'].astype(str).replace('\.0', '', regex=True)
#df['Max'] = (df['mz_node'] / df['mzlow']).apply(np.floor)
#df['Max'] = df['Max'].astype(str).replace('\.0', '', regex=True)

# Can be manually defined in the output analyte list for LacyTools
df['Calibrant'] = ''

#final output order
df = df[['# Peak', 'RT', 'Mass Window', 'Time Window', 'Min Charge', 'Max', 'Calibrant']]

# export as csv with tab separation
df.to_csv("LacyToolsAnalyteList.csv", index=False, sep="\t")